# Unity Catalog: Data Discovery

## Bloque 6: Visualizar Relaciones entre Tablas

``Tenga en cuenta`` Para poder ejecutar el bloque 6 es necesario crear el job ``courseUC_sesion3`` disponible el yaml en el repositorio GIT

In [0]:
%sql
--Hemos hecho unos ajustes en el JOB. Limpiemos las tablas plata para correr el JOB con nuestro YAML desde 0
drop schema if exists sesion1_2.layer20_bronze cascade;
create schema if not exists sesion1_2.layer20_bronze;

drop schema if exists sesion1_2.layer30_silver cascade;
create schema if not exists sesion1_2.layer30_silver;

drop schema if exists sesion1_2.layer30_silver_quarantine cascade;
create schema if not exists sesion1_2.layer30_silver_quarantine;

El **Objetivo del Bloque 6** --> Visualizar las relaciones entre tablas

1. Una vez creamos las distintas claves primarias y foraneas entre tablas, databricks nos permite visualizar esta relacion.


### 6.1 Creacion de claves primarias y foraneas

#### 6.1.1 dim_phase

In [0]:
%sql
select * from sesion1_2.layer30_silver.dim_phase

phase_key phase_name category exp_ias_min_kts exp_ias_max_kts exp_alt_min_ft exp_alt_max_ft description PARKED Parked ground null null -1000 100 Aircraft at gate/standstill TAXI Taxi ground 0.0 30.0 -1000 200 Ground movement to/from runway TAKEOFF Takeoff air 80.0 200.0 0 3000 Acceleration and liftoff CLIMB Climb air 150.0 350.0 1000 20000 Climb to cruise altitude CRUISE Cruise air 200.0 550.0 10000 45000 Level flight at cruise altitude DESCENT Descent air 150.0 450.0 500 35000 Descent from cruise APPROACH Approach air 120.0 250.0 0 8000 Final approach procedures LANDING Landing air 80.0 180.0 0 2000 Touchdown and rollout

In [0]:
  %sql
-- Evita nulos a nivel de metadatos
ALTER TABLE sesion1_2.layer30_silver.dim_phase
  ALTER COLUMN phase_key SET NOT NULL;

-- Crea la primary key (fallará si quedan duplicados)
ALTER TABLE sesion1_2.layer30_silver.dim_phase
  ADD CONSTRAINT pk_dim_phase PRIMARY KEY (phase_key);


#### 6.1.2 dim_aircrat

In [0]:
%sql
select * from sesion1_2.layer30_silver.dim_aircraft

aircraft_id tail_number model manufacturer engine_model first_service_dt status cycles_total hours_total A00001 EC-001AB A350-900 Airbus GEnx-1B 2018-12-23 active 30089 5878 A00002 EC-002AB B787-9 Boeing CFM56-7B 2018-04-05 active 13349 38999 A00003 EC-003AB A350-900 Airbus Trent XWB 2011-10-07 maintenance 47364 23814 A00004 EC-004AB B737-800 Boeing Trent XWB 2010-08-14 storage 24254 52272 A00005 EC-005AB E190 Embraer GEnx-1B 2018-01-10 active 26984 19151 A00006 EC-006AB E190 Embraer GE CF34 2014-02-14 maintenance 24604 45561 A00007 EC-007AB A350-900 Airbus CFM56-7B 2021-08-20 active 998 77414 A00008 EC-008AB B737-800 Boeing GE CF34 2012-07-07 active 42411 29007 A00009 EC-009AB A350-900 Airbus GE CF34 2023-08-01 maintenance 27364 61683 A00010 EC-010AB E190 Embraer GEnx-1B 2020-04-19 active 43246 27031 A00011 EC-011AB B787-9 Boeing GEnx-1B 2020-02-19 active 4928 73119 A00012 EC-012AB E190 Embraer GEnx-1B 2014-09-26 active 6358 5298 A00013 EC-013AB E190 Embraer CFM56-7B 2013-09-14 active 15637 64252 A00014 EC-014AB A350-900 Airbus Trent XWB 2016-08-01 active 23019 36950 A00015 EC-015AB A350-900 Airbus CFM56-7B 2019-04-04 maintenance 40376 70295 A00016 EC-016AB A350-900 Airbus GE CF34 2021-03-26 maintenance 7711 25338 A00017 EC-017AB A350-900 Airbus GE CF34 2023-10-18 maintenance 32238 19777 A00018 EC-018AB B787-9 Boeing GEnx-1B 2022-05-07 active 6736 27631 A00019 EC-019AB B737-800 Boeing GE CF34 2010-08-05 active 30458 30552 A00020 EC-020AB B787-9 Boeing GEnx-1B 2018-09-26 maintenance 20801 73225 A00021 EC-021AB B787-9 Boeing GE CF34 2015-11-25 active 49198 74827 A00022 EC-022AB A320-200 Airbus CFM56-7B 2018-12-24 active 45228 54432 A00023 EC-023AB B787-9 Boeing GEnx-1B 2013-09-21 active 6723 14664 A00024 EC-024AB A350-900 Airbus GEnx-1B 2022-10-18 active 14720 72097

In [0]:
%sql
-- Evita nulos a nivel de metadatos
ALTER TABLE sesion1_2.layer30_silver.dim_aircraft
  ALTER COLUMN aircraft_id SET NOT NULL;

-- Crea la primary key (fallará si quedan duplicados)
ALTER TABLE sesion1_2.layer30_silver.dim_aircraft
  ADD CONSTRAINT pk_aircraft_id PRIMARY KEY (aircraft_id);

#### 6.1.3 dim_sensor_reading

In [0]:
%sql
select * from sesion1_2.layer30_silver.dim_sensor_reading

reading_id sensor_type unit quality_flag source_system calibration_version reading_ts R000001 IAS kts OK ACMS v1.0 2025-01-01T08:00:00.000Z R000002 ALT ft OK ACMS v1.1 2025-01-01T08:05:00.000Z R000003 IAS kts OK ACMS v1.0 2025-01-01T08:10:00.000Z R000004 ALT ft OK FDR v2.0 2025-01-01T08:15:00.000Z R000005 OAT C OK FDR null 2025-01-01T08:20:00.000Z R000006 ALT ft OK ACMS v1.0 2025-01-01T08:25:00.000Z R000007 ALT ft OK ACMS v1.1 2025-01-01T08:30:00.000Z R000008 IAS kts SUSPECT FDR v2.0 2025-01-01T08:35:00.000Z R000009 IAS kts OK FDR null 2025-01-01T08:40:00.000Z R000010 IAS kts OK ACMS v1.0 2025-01-01T08:45:00.000Z R000011 ALT ft OK FDR v1.0 2025-01-01T08:50:00.000Z R000012 ALT ft OK FDR null 2025-01-01T08:55:00.000Z R000013 IAS kts OK ACMS null 2025-01-01T09:00:00.000Z R000014 IAS kts OK FDR v1.0 2025-01-01T09:05:00.000Z R000015 IAS kts OK ACMS v1.1 2025-01-01T09:10:00.000Z R000016 OAT C OK ACMS v2.0 2025-01-01T09:15:00.000Z R000017 IAS kts OK FDR v2.0 2025-01-01T09:20:00.000Z R000018 IAS kts OK FDR v1.0 2025-01-01T09:25:00.000Z R000019 OAT C OK ACMS v2.0 2025-01-01T09:30:00.000Z R000020 IAS kts OK ACMS v2.0 2025-01-01T09:35:00.000Z R000021 ALT ft BAD ACMS v1.1 2025-01-01T09:40:00.000Z R000022 OAT C OK ACMS v1.0 2025-01-01T09:45:00.000Z R000023 IAS kts OK FDR v1.0 2025-01-01T09:50:00.000Z R000024 ALT ft OK ACMS v1.0 2025-01-01T09:55:00.000Z R000025 OAT C OK ACMS v2.0 2025-01-01T10:00:00.000Z R000026 IAS kts OK FDR v1.0 2025-01-01T10:05:00.000Z R000027 ALT ft BAD FDR v1.0 2025-01-01T10:10:00.000Z R000028 ALT ft SUSPECT FDR v1.1 2025-01-01T10:15:00.000Z R000029 ALT ft SUSPECT ACMS v1.0 2025-01-01T10:20:00.000Z R000030 IAS kts OK ACMS v1.0 2025-01-01T10:25:00.000Z R000031 IAS kts SUSPECT ACMS v1.0 2025-01-01T10:30:00.000Z R000032 IAS kts OK ACMS v1.1 2025-01-01T10:35:00.000Z R000033 IAS kts OK ACMS v2.0 2025-01-01T10:40:00.000Z R000034 IAS kts OK ACMS v1.1 2025-01-01T10:45:00.000Z R000035 IAS kts OK FDR v1.0 2025-01-01T10:50:00.000Z R000036 ALT ft OK FDR v1.0 2025-01-01T10:55:00.000Z R000037 ALT ft OK ACMS v1.1 2025-01-01T11:00:00.000Z R000038 IAS kts OK ACMS null 2025-01-01T11:05:00.000Z R000039 ALT ft OK ACMS null 2025-01-01T11:10:00.000Z R000040 IAS kts OK ACMS v1.0 2025-01-01T11:15:00.000Z

In [0]:
%sql
-- Evita nulos a nivel de metadatos
ALTER TABLE sesion1_2.layer30_silver.dim_sensor_reading
  ALTER COLUMN reading_id SET NOT NULL;

-- Crea la primary key (fallará si quedan duplicados)
ALTER TABLE sesion1_2.layer30_silver.dim_sensor_reading
  ADD CONSTRAINT pk_reading_id PRIMARY KEY (reading_id);

#### 6.1.4 fact_engine_sensor

In [0]:
%sql
-- FACT: PK y FKs no nulas
ALTER TABLE sesion1_2.layer30_silver.fact_engine_sensor ALTER COLUMN reading_id       SET NOT NULL;
ALTER TABLE sesion1_2.layer30_silver.fact_engine_sensor ALTER COLUMN aircraft_id      SET NOT NULL;
ALTER TABLE sesion1_2.layer30_silver.fact_engine_sensor ALTER COLUMN phase_of_flight  SET NOT NULL;


-- FACT (definimos primary key en fact table)
ALTER TABLE sesion1_2.layer30_silver.fact_engine_sensor
ADD CONSTRAINT pk_fact_engine_sensor PRIMARY KEY (reading_id);


-- FK: fact.aircraft_id → dim_aircraft.aircraft_id
ALTER TABLE sesion1_2.layer30_silver.fact_engine_sensor
ADD CONSTRAINT fk_fact_engine_sensor_aircraft
FOREIGN KEY (aircraft_id)
REFERENCES sesion1_2.layer30_silver.dim_aircraft(aircraft_id);

-- FK: fact.phase_of_flight → dim_phase.phase_key
ALTER TABLE sesion1_2.layer30_silver.fact_engine_sensor
ADD CONSTRAINT fk_fact_engine_sensor_phase
FOREIGN KEY (phase_of_flight)
REFERENCES sesion1_2.layer30_silver.dim_phase(phase_key);

-- FK: fact.reading_id → dim_sensor_reading.reading_id
ALTER TABLE sesion1_2.layer30_silver.fact_engine_sensor
ADD CONSTRAINT fk_fact_engine_sensor_reading
FOREIGN KEY (reading_id)
REFERENCES sesion1_2.layer30_silver.dim_sensor_reading(reading_id);


### 6.2 Visualizar relacion

Databricks permite definir y visualizar relaciones entre tablas directamente desde Unity Catalog, utilizando constraints de tipo Primary Key (PK) y Foreign Key (FK).

Estas relaciones no solo documentan el modelo de datos, sino que además refuerzan la integridad referencial y facilitan el análisis visual de dependencias.

<img src="https://raw.githubusercontent.com/jmartinezceste/251101Course_UC_Ceste/main/photos/view_relationship.png" width="800">

## Bloque 7: Uso de Genie

### 7.1 🤖 Introducción a Databricks Genie

**Genie** es el agente conversacional de **Databricks** diseñado para interactuar con tus datos mediante lenguaje natural.  
En lugar de escribir consultas SQL, puedes simplemente *preguntar* y Genie genera automáticamente las queries necesarias, interpretando tus intenciones y usando el contexto de tu workspace.


### 7.2 ¿Qué hace Genie?

Genie utiliza el modelo de inteligencia artificial integrado en la **Databricks Data Intelligence Platform** para:

- **Comprender el contexto** de tus catálogos, esquemas y tablas registradas en Unity Catalog.  
- **Generar consultas SQL precisas** en función de tus preguntas.  
- **Analizar datos, resumir tendencias y explicar resultados** directamente en lenguaje natural.  
- **Aprender del entorno**, usando metadatos, descripciones y ejemplos guardados en tu workspace.  



### 7.3 ¿Por qué es útil?

Genie te permite:
- Explorar tus datos sin necesidad de conocer SQL o Spark.  
- Validar hipótesis rápidamente durante una demo o análisis exploratorio.  
- Generar visualizaciones simples desde lenguaje natural.  
- Crear una experiencia más accesible para usuarios de negocio dentro del entorno Databricks.

### 7.4 Ejemplo

#### 7.4.1 Abrir un espacio GENIE

##### 7.4.1.1 Puedes iniciar Genie desde el Menu o desde una tabla ya creada

%md
<img src="https://raw.githubusercontent.com/jmartinezceste/251101Course_UC_Ceste/main/photos/genie step1.png" width="800">

##### 7.4.1.2 Selecciona las tablas las cuales formarar parte del espacio

%md
<img src="https://raw.githubusercontent.com/jmartinezceste/251101Course_UC_Ceste/main/photos/genie step2 tablas.png" width="800">

##### 7.4.1.3 Preguntas de ejemplo

In [0]:
# 💬 Ejemplos de preguntas para usar con Genie
# Estas consultas están pensadas para probar el agente una vez creadas las tablas:
# dim_aircraft, dim_phase, dim_sensor_reading y fact_sensor

# 1️⃣ ¿Qué modelo de aeronave acumula más horas totales de vuelo?
# → Usa la tabla dim_aircraft y la columna hours_total
question_1 = "¿Qué modelo de aeronave acumula más horas totales de vuelo?"

# 2️⃣ Muéstrame las fases de vuelo con mayor número de lecturas de sensor.
# → Cruza fact_sensor con dim_phase por phase_key o phase_id
question_2 = "Muéstrame las fases de vuelo con mayor número de lecturas de sensor."

# 3️⃣ ¿En qué fase del vuelo suelen registrarse las altitudes más altas?
# → Usa fact_sensor.altitude y dim_phase.phase_name
question_3 = "¿En qué fase del vuelo suelen registrarse las altitudes más altas?"

# 4️⃣ ¿Existen sensores con valores fuera de rango o anomalías en velocidad?
# → Consulta fact_sensor.speed_knots y detecta valores > 600 nudos
question_4 = "¿Existen sensores con valores fuera de rango o anomalías en velocidad?"

# 5️⃣ Dame un resumen de las condiciones del sensor para aeronaves con más de 20.000 horas de vuelo.
# → Combina dim_aircraft (filtro por horas) y fact_sensor (promedios de temperatura, velocidad, etc.)
question_5 = "Dame un resumen de las condiciones del sensor para aeronaves con más de 20.000 horas de vuelo."


# Unity Catalog: Data Sharing

## Bloque 8: Delta Sharing

### 8.1 Delta Sharing

### 8.2 Marketplace

### 8.3 Databricks Clean Rooms

# Unity Catalog: Data Auditing

## Bloque 9: Systems Table

### 9.1 State of Objects

#### 9.1.1 Cuales son las todas las Tablas en el Catalogo X?

In [0]:
%sql
select table_name
from system.information_schema.tables
where table_catalog="sesion1_2"
and table_schema!="information_schema"

table_name sales_clean dim_phase fact_engine_sensor_quarantine fact_maintenance_event_quarantine v_quarantine_rate_dim_aircraft dim_aircraft_quarantine sales_quarantine dim_phase fact_engine_sensor fact_engine_sensor sales_kpi dim_sensor_reading sales_raw fact_maintenance_event dim_sensor_reading fact_maintenance_event dim_aircraft dim_sensor_reading_quarentine dim_phase_quarantine dim_aircraft_models dim_aircraft

#### 9.1.2 Quien tiene acceso a esa tabla?

In [0]:
%sql
-- Quien tiene acceso a esa tabla

SELECT grantee, table_name, privilege_type
FROM system.information_schema.table_privileges
WHERE table_name = 'dim_aircraft'

grantee table_name privilege_type

#### 9.1.3 Quien fue el ultimo en actualizar las tabla plata y cuando

In [0]:
%sql

SELECT table_name,last_altered_by,last_altered
FROM system.information_schema.tables
WHERE table_schema ="layer30_silver"
ORDER BY 1,3 DESC;

table_name last_altered_by last_altered dim_aircraft 251008javiceste@gmail.com 2025-10-31T18:27:29.094Z dim_aircraft_models 251008javiceste@gmail.com 2025-10-31T18:26:35.280Z dim_phase 251008javiceste@gmail.com 2025-10-31T18:27:29.584Z dim_restaurants 251008javiceste@gmail.com 2025-10-21T15:13:25.051Z dim_sensor_reading 251008javiceste@gmail.com 2025-10-31T18:27:30.039Z fact_engine_sensor 251008javiceste@gmail.com 2025-10-31T18:27:30.050Z fact_maintenance_event 251008javiceste@gmail.com 2025-10-28T19:59:01.454Z menu_all_enriched 251008javiceste@gmail.com 2025-10-21T15:13:27.645Z menu_completo_all 251008javiceste@gmail.com 2025-10-21T15:13:08.351Z menu_completo_v1 251008javiceste@gmail.com 2025-10-21T15:13:06.151Z menu_completo_v2 251008javiceste@gmail.com 2025-10-21T15:13:03.838Z sales_clean 251008javiceste@gmail.com 2025-10-19T08:01:05.939Z sales_clean 251008javiceste@gmail.com 2025-10-19T07:59:05.567Z sales_quarantine 251008javiceste@gmail.com 2025-10-19T08:01:08.352Z sales_quarantine 251008javiceste@gmail.com 2025-10-19T07:59:07.917Z vw_menu_all_enriched_min 251008javiceste@gmail.com 2025-10-21T15:13:32.514Z

#### 9.1.4 Quien es el owner de esa tabla?

In [0]:
%sql
SELECT table_owner
FROM system.information_schema.tables
WHERE table_catalog ="sesion1_2" and table_schema ="layer30_silver"
and table_name="dim_aircraft"

table_owner 251008javiceste@gmail.com

### 9.2 Audit Logs

#### 9.2.1 Quien accede a esta tabla con mas frecuencia?

In [0]:
%sql
SELECT user_identity.email, count(*)
FROM system.access.audit
WHERE request_params.table_full_name = "sesion1_2.layer30_silver.dim_aircraft"
AND service_name = "unityCatalog"
AND action_name = "generateTemporaryTableCredential"
GROUP BY 1 ORDER BY 2 DESC LIMIT 1;

email count(*) 251008javiceste@gmail.com 203

#### 9.2.2 Quien borro esta tabla?

In [0]:
%sql
SELECT user_identity.email
FROM system.access.audit
WHERE request_params.full_name_arg = "sesion1_2.layer30_silver.dim_aircraft"
AND service_name = "unityCatalog"
AND action_name = "deleteTable"

email 251008javiceste@gmail.com 251008javiceste@gmail.com

In [0]:
%sql
select *
from system.access.audit

account_id workspace_id version event_time event_date source_ip_address user_agent session_id user_identity service_name action_name request_id request_params response audit_level event_id identity_metadata 3e454ef6-0234-431e-bba1-372858b87e1c 1330931038747594 2.0 2025-10-19T15:20:32.904Z 2025-10-19 10.41.58.240 armeria/1.30.3 null List(System-User, null) clusters delete a02304a3-1bd1-4697-9fc9-d7d462d44a7a Map(cluster_id -> 1019-150815-c7erejx6-v2n) List(200, null, {}) WORKSPACE_LEVEL 621a45fe-c2d1-37f1-a20a-964f0bc3e709 List(null, null, null) 3e454ef6-0234-431e-bba1-372858b87e1c 0 2.0 2025-10-19T15:08:31.760Z 2025-10-19 172.21.153.199 Apache-HttpClient/4.5.14 (Java/17.0.15) Databricks-Service/driver RawDBHttpClient/apply null List(251008javiceste@gmail.com, null) unityCatalog getSchema e88fb2ad-fc15-43ec-ad1c-83b9aecd01cf Map(full_name_arg -> airline_demo.silver, include_manifest_capabilities -> true, metastore_id -> 24251221-5fcd-4ccf-90bc-f7e819553b47, workspace_id -> 1330931038747594) List(200, null, {"name":"silver","schema_id":"646f352f-dd60-4f6f-9ba7-b6cdba7f0f8d"}) ACCOUNT_LEVEL 46f7058c-6273-36b6-b17f-d983028fdbca List(251008javiceste@gmail.com, 251008javiceste@gmail.com, null) 3e454ef6-0234-431e-bba1-372858b87e1c 0 2.0 2025-10-19T15:08:31.725Z 2025-10-19 172.21.153.199 Apache-HttpClient/4.5.14 (Java/17.0.15) Databricks-Service/driver RawDBHttpClient/apply null List(251008javiceste@gmail.com, null) unityCatalog getCatalog 4088ae03-212d-4509-8381-a1a3efa9d24e Map(include_manifest_capabilities -> true, metastore_id -> 24251221-5fcd-4ccf-90bc-f7e819553b47, name_arg -> airline_demo, workspace_id -> 1330931038747594) List(200, null, {"id":"7e104895-6a66-40b9-a786-545fff2d91d3"}) ACCOUNT_LEVEL c765fdbb-7e01-373d-acc4-a18907245ad9 List(251008javiceste@gmail.com, 251008javiceste@gmail.com, null) 3e454ef6-0234-431e-bba1-372858b87e1c 0 2.0 2025-10-19T15:08:49.119Z 2025-10-19 172.21.153.199 Apache-HttpClient/4.5.14 (Java/17.0.15) Databricks-Service/driver RawDBHttpClient/apply null List(251008javiceste@gmail.com, null) unityCatalog getVolume 839a77cd-6e73-45cc-b7dd-3e348330bf92 Map(include_manifest_capabilities -> true, metastore_id -> 24251221-5fcd-4ccf-90bc-f7e819553b47, volume_full_name -> airline_demo.default.data, workspace_id -> 1330931038747594) List(404, DatabricksServiceException: RESOURCE_DOES_NOT_EXIST: Volume 'airline_demo.default.data' does not exist., null) ACCOUNT_LEVEL d05c427f-5a5d-36f3-a413-5d59606fafdf List(251008javiceste@gmail.com, 251008javiceste@gmail.com, null) 3e454ef6-0234-431e-bba1-372858b87e1c 0 2.0 2025-10-19T15:08:30.336Z 2025-10-19 172.21.153.199 Apache-HttpClient/4.5.14 (Java/17.0.15) Databricks-Service/driver RawDBHttpClient/apply null List(251008javiceste@gmail.com, null) unityCatalog createCatalog a3d29647-4f7d-4919-a6ec-74285d455116 Map(name -> airline_demo, include_manifest_capabilities -> true, comment -> , storage_mode -> DEFAULT_STORAGE, workspace_id -> 1330931038747594, metastore_id -> 24251221-5fcd-4ccf-90bc-f7e819553b47) List(400, DatabricksServiceException: CATALOG_ALREADY_EXISTS: Catalog 'airline_demo' already exists, null) ACCOUNT_LEVEL 5204e890-7d8c-373d-a9d9-57f3146dfd9f List(251008javiceste@gmail.com, 251008javiceste@gmail.com, null) 3e454ef6-0234-431e-bba1-372858b87e1c 0 2.0 2025-10-19T15:09:48.955Z 2025-10-19 172.21.153.199 Apache-HttpClient/4.5.14 (Java/17.0.15) Databricks-Service/driver RawDBHttpClient/apply null List(251008javiceste@gmail.com, null) unityCatalog getVolume 7d4841cd-98f8-4e7c-8e8d-afba40294f97 Map(include_manifest_capabilities -> true, metastore_id -> 24251221-5fcd-4ccf-90bc-f7e819553b47, volume_full_name -> airline_demo.default.data, workspace_id -> 1330931038747594) List(404, DatabricksServiceException: RESOURCE_DOES_NOT_EXIST: Volume 'airline_demo.default.data' does not exist., null) ACCOUNT_LEVEL 6e194b83-3a10-3419-a8d5-c7685f0d0441 List(251008javiceste@gmail.com, 251008javiceste@gmail.com, null) 3e454ef6-0234-431e-bba1-372858b87e1c 0 2.0 2025-10-19T15:09:

In [0]:
%sql
select distinct(action_name)
from system.access.audit

action_name runNow deltaSharingProxyQueryTable fileEditorOpenEvent getInformationSchema getTableById requestPermissions getHistoryQueriesByLookupKeys createFunction createConstraint legacyListTagPolicies accountlessToAccountLoginAuthentication listExternalMetadata tokenLogin accountLoginCodeAuthentication listTables updateTables legacyDeleteTagPolicy UpdateCatalogWorkspaceBindings getSchema fileDelete getVolume deltaSharingProxyGetTableMetadata filesGet runTriggered deleteResourceSuccess legacyCreateTagPolicy list importNotebook updatePermissions moveWorkspaceNode createGroup createMetastore runFailed getFrequentQueryByTable mintOAuthAuthorizationCode createSchema createSpace filesDelete createInstruction getTagSubentityAssignments listSecurableByEntityEvent oidcBrowserLogin listRegisteredModels createNotebook createDownloadUrl moveNotebook detachNotebook createMetastoreAssignment getCurrentMetastoreAssignment listExternalLineages deleteSchema updatePermissionAssignment getRunOutput renameNotebook listEntityLineagesBySecurable filesPut getFrequentUserByTable modifyNotebook getPublishedDashboard deleteCatalog legacyGetTagPolicy deleteTable listProviders deleteNotebook deleteRepo listTableSummaries cancelQuery setSetting activateProvider wsfsImportFile getTablePopularityByDate generateTemporaryVolumeCredential cloneNotebook createCatalog update getTagSecurableAssignments startEndpoint getTable createFolder UpdateTagSecurableAssignments listSecurableTags filesHead createTable metadataAndPermissionsSnapshot getSecret getFrequentlyJoinedTables createStagingTable getQueryResult submitCommand delete listColumnLineages attachNotebook changeClusterAcl listCatalogs PutMetrics RetrieveManagedEncryptionKeys tableExists createDashboard listSchemas listCredentials updateUser enableSystemSchema getFunction createVolume listVolumes listSecurableLineagesBySecurable cancel wsfsStreamingRead getStatus getPopularEntities listFunctions executeQuery updateRuleSet cancelAllRuns submitRun create createRepo updateSampleQuestions purgeWorkspaceNodes getPopularTables addPrincipalToGroup getMetastoreSummary changeJobAcl fileCreate runSucceeded updateCatalog getCatalog workspaceExport deleteFunction updateAutoMaintenancePermissions runStart getForeignCredentials generateTemporaryTableCredential wsfsStreamingWrite authzEval listConnections listExternalLocations renameWorkspaceNode listRecipients getEffectivePermissions updateSchema reset createUploadUrl add moveFolder getMetastore openNotebook getExternalLocation listShares getDefaultDestinationStatus updateMetastore deleteConstraint repairRun generateDbToken listGitCredentials

#### 9.2.3 ¿a qué ha accedido este usuario en las ultimas 24h?

In [0]:
%sql
SELECT 
  date_format(event_time, 'yyyy-MM-dd HH:mm:ss') AS event_time_local,
  action_name
FROM system.access.audit
WHERE user_identity.email = "251009javiceste@gmail.com"
  AND service_name = "unityCatalog"
  AND event_date > current_date() - INTERVAL 1 DAY
ORDER BY event_time DESC;


event_time_local action_name 2025-10-31 19:13:46 getInformationSchema 2025-10-31 19:13:45 metadataAndPermissionsSnapshot 2025-10-31 19:13:45 metadataAndPermissionsSnapshot 2025-10-31 19:13:45 metadataAndPermissionsSnapshot 2025-10-31 19:13:45 metadataAndPermissionsSnapshot 2025-10-31 19:13:44 getTable 2025-10-31 19:12:58 listCatalogs 2025-10-31 19:12:27 listSchemas 2025-10-31 19:12:27 listTables 2025-10-31 19:10:04 getInformationSchema 2025-10-31 19:10:04 metadataAndPermissionsSnapshot 2025-10-31 19:10:04 metadataAndPermissionsSnapshot 2025-10-31 19:10:04 metadataAndPermissionsSnapshot 2025-10-31 19:10:04 metadataAndPermissionsSnapshot 2025-10-31 19:10:03 getTable 2025-10-31 19:10:03 getTable 2025-10-31 19:10:02 getTable 2025-10-31 19:09:57 getInformationSchema 2025-10-31 19:09:57 metadataAndPermissionsSnapshot 2025-10-31 19:09:57 metadataAndPermissionsSnapshot 2025-10-31 19:09:57 getTable 2025-10-31 19:09:57 metadataAndPermissionsSnapshot 2025-10-31 19:09:57 metadataAndPermissionsSnapshot 2025-10-31 19:09:56 getTable 2025-10-31 19:09:54 getTable 2025-10-31 19:09:38 getInformationSchema 2025-10-31 19:09:38 metadataAndPermissionsSnapshot 2025-10-31 19:09:38 metadataAndPermissionsSnapshot 2025-10-31 19:09:38 metadataAndPermissionsSnapshot 2025-10-31 19:09:38 metadataAndPermissionsSnapshot 2025-10-31 19:09:37 getTable 2025-10-31 19:09:36 getTable 2025-10-31 19:09:35 getTable 2025-10-31 19:09:32 getTable 2025-10-31 19:09:31 listTables 2025-10-31 19:09:31 listSchemas 2025-10-31 19:09:28 getTable 2025-10-31 19:09:27 getVolume 2025-10-31 19:09:27 getTable 2025-10-31 19:09:26 getTable 2025-10-31 19:09:26 getVolume 2025-10-31 19:09:25 getTable 2025-10-31 19:09:24 getTable 2025-10-31 19:09:24 getTable 2025-10-31 19:09:22 getTable 2025-10-31 19:09:21 getTable 2025-10-31 19:09:19 getTable 2025-10-31 19:09:14 getTable 2025-10-31 19:09:14 getTable 2025-10-31 19:09:13 getTable 2025-10-31 19:09:12 getTable 2025-10-31 19:09:09 getTable 2025-10-31 19:09:03 listSchemas 2025-10-31 19:09:01 getSchema 2025-10-31 19:09:01 getSchema 2025-10-31 19:09:01 getCatalog 2025-10-31 19:09:01 getCurrentMetastoreAssignment 2025-10-31 19:08:55 getTable 2025-10-31 19:08:55 getTable 2025-10-31 19:08:54 getTable 2025-10-31 19:08:53 getTable 2025-10-31 19:08:52 getTable 2025-10-31 19:08:51 getTable 2025-10-31 19:08:49 getTable 2025-10-31 19:08:44 getTable 2025-10-31 19:08:43 getTable 2025-10-31 19:08:43 getTable 2025-10-31 19:08:43 getVolume 2025-10-31 19:08:43 getTable 2025-10-31 19:08:43 getTable 2025-10-31 19:08:42 getVolume 2025-10-31 19:08:30 getVolume 2025-10-31 19:08:27 getVolume 2025-10-31 19:08:27 getVolume 2025-10-31 19:08:24 getVolume 2025-10-31 19:08:15 getSchema 2025-10-31 19:08:15 getCatalog 2025-10-31 19:08:14 getSchema 2025-10-31 19:08:14 getCatalog 2025-10-31 19:08:14 getSchema 2025-10-31 19:08:14 getCatalog 2025-10-31 19:08:14 createCatalog 2025-10-31 19:07:53 listCatalogs 2025-10-31 19:05:51 getInformationSchema 2025-10-31 19:05:51 metadataAndPermissionsSnapshot 2025-10-31 19:05:50 metadataAndPermissionsSnapshot 2025-10-31 19:05:50 metadataAndPermissionsSnapshot 2025-10-31 19:05:50 metadataAndPermissionsSnapshot 2025-10-31 19:05:50 getTable 2025-10-31 19:05:50 getTable 2025-10-31 19:05:48 getTable 2025-10-31 19:05:48 getTable 2025-10-31 19:05:47 getTable 2025-10-31 19:05:47 getTable 2025-10-31 19:05:47 getTable 2025-10-31 19:05:47 getTable 2025-10-31 19:05:47 getTable 2025-10-31 19:05:47 getTable 2025-10-31 19:05:46 getTable 2025-10-31 19:05:46 getTable 2025-10-31 19:05:45 getTable 2025-10-31 19:05:45 getTable 2025-10-31 19:05:45 getTable 2025-10-31 19:05:45 getTable 2025-10-31 19:05:45 getTable 2025-10-31 19:05:45 getTable 2025-10-31 19:05:37 getInformationSchema 2025-10-31 19:05:36 metadataAndPermissionsSnapshot 2025-10-31 19:05:36 metadataAndPermissionsSnapshot 2025-10-31 19:05:36 metadataAndPermissionsSnapshot 2025-10-31 19:05:36 metadataAndPermissionsSnapshot 2025-10-31 19:05:36 getTable 2025-10-31 19:05:36 getTable 2025-10-31 19:05:36 getTab

#### 9.2.4 A que tablas accede este usuario con mas frecuencia?

In [0]:
%sql
SELECT request_params.table_full_name, count(*)
FROM system.access.audit
WHERE user_identity.email = "251009javiceste@gmail.com"
AND service_name = "unityCatalog"
GROUP BY 1 ORDER BY 2 DESC LIMIT 10;


table_full_name count(*) null 45361 airline_demo.bronze.flights 521 airline_demo.silver.flights_enriched 521 airline_demo.bronze.airports 521 airline_demo.gold.delay_summary 349 sesion1_2.layer30_silver.dim_aircraft 311 sesion1_2.layer30_silver_quarantine.dim_aircraft_quarantine 129 sesion1_2.layer30_silver_quarantine.fact_engine_sensor_quarantine 111 sesion1_2.layer30_silver.fact_engine_sensor 101 sesion1_2.layer20_bronze.fact_engine_sensor 81

### 9.3 Billing Logs

#### 9.3.1 Cual es la tendencia de consumo diario en DBU?

In [0]:
%sql
SELECT
  DATE(usage_start_time) AS usage_date,
  SUM(usage_quantity) AS dbus_consumed
FROM system.billing.usage
WHERE usage_unit = 'DBU'
GROUP BY DATE(usage_start_time)
ORDER BY usage_date ASC;


usage_date dbus_consumed 2025-10-08 6.132220423809523950 2025-10-09 13.077892122815094786 2025-10-10 6.049786114285714119 2025-10-13 5.620341194047619158 2025-10-14 8.108407674999999986 2025-10-15 8.355810532142857174 2025-10-16 8.292160457142857149 2025-10-17 3.023192585714285714 2025-10-18 1.118860125000000040 2025-10-19 9.446595785837939128 2025-10-20 3.544856041428571428 2025-10-21 7.759000655181730267 2025-10-22 7.015383204840085789 2025-10-23 5.318900117515682511 2025-10-24 5.825544603730158707 2025-10-25 1.133658952777777778 2025-10-26 9.237254201111111105 2025-10-27 0.647741066666666620 2025-10-28 4.492209780158730216 2025-10-29 1.722316896666666624 2025-10-30 0.412186775000000000 2025-10-31 11.826744275199083466 2025-11-01 0.132044500000000000

#### 9.3.2 Top 10 usuarios que más DBUs consumen

In [0]:
%sql
SELECT
  COALESCE(custom_tags['Creator'], custom_tags['Owner'], 'unknown') AS User,
  SUM(usage_quantity) AS DBUs
FROM system.billing.usage
WHERE usage_unit = 'DBU'
GROUP BY 1
ORDER BY DBUs DESC
LIMIT 10;


User DBUs unknown 128.293108086072155715

In [0]:
%sql
--Alternativa por Jobs (si no tienes tags): unir con metadatos del job para obtener run_as:
SELECT
  j.run_as AS User,
  SUM(u.usage_quantity) AS DBUs
FROM system.billing.usage u
JOIN system.lakeflow.jobs j
  ON CAST(u.usage_metadata.job_id AS STRING) = CAST(j.job_id AS STRING)
WHERE u.usage_unit = 'DBU'
GROUP BY j.run_as
ORDER BY DBUs DESC
LIMIT 10;

User DBUs 78102164661613 79149.960184120452309642

#### 9.3.3 DBUs por SKU en el mes actual

In [0]:
%sql
SELECT
  sku_name              AS SKU,
  SUM(usage_quantity)   AS DBUs
FROM system.billing.usage
WHERE usage_unit = 'DBU'
  AND DATE_TRUNC('month', usage_start_time) = DATE_TRUNC('month', CURRENT_DATE())
GROUP BY sku_name
ORDER BY DBUs DESC;

SKU DBUs PREMIUM_JOBS_SERVERLESS_COMPUTE_US_EAST_OHIO 0.132044500000000000

#### 9.3.4 Qué Jobs consumieron más DBUs


In [0]:
%sql
SELECT
  CAST(usage_metadata.job_id AS STRING) AS `Job ID`,
  SUM(usage_quantity)                   AS DBUs
FROM system.billing.usage
WHERE usage_unit = 'DBU'
  AND usage_metadata.job_id IS NOT NULL
GROUP BY CAST(usage_metadata.job_id AS STRING)
ORDER BY DBUs DESC;


Job ID DBUs 198707480380341 35.562914635714285723 477608695616861 7.641684703062523469 627651429132980 4.753752882142857162 655309120384121 2.620310091869083646 1089664726913441 1.967098403571428535 106091754903049 0.560695000000000000 460790114114136 0.298574360714285733

### 9.4 Lineage Data

#### 9.4.1 Qué tablas se crean a partir de una tabla origen — descendencia

``esta NO funcionan en version free``

In [0]:
%sql
SELECT DISTINCT
  target_table_full_name
FROM
  system.lakeflow.table_lineage
WHERE
  source_table_name = 'login_data_bronze';




---------------------------------------------------------------------------
AnalysisException                         Traceback (most recent call last)
File <command-8798613454692251>, line 1
----> 1 get_ipython().run_cell_magic('sql', '', "-- Qué tablas se crean (target) a partir de login_data_bronze\nSELECT DISTINCT\n  target_table_full_name\nFROM system.data_lineage.table_lineage\nWHERE source_table_full_name = 'main.dbdemos_lhm.login_data_bronze';\n")

File /databricks/python/lib/python3.12/site-packages/IPython/core/interactiveshell.py:2541, in InteractiveShell.run_cell_magic(self, magic_name, line, cell)
   2539 with self.builtin_trap:
   2540     args = (magic_arg_s, cell)
-> 2541     result = fn(*args, **kwargs)
   2543 # The code below prevents the output from being displayed
   2544 # when using magics with decorator @output_can_be_silenced
   2545 # when the last Python token in the expression is a ';'.
   2546 if getattr(fn, magic.MAGIC_OUTPUT_CAN_BE_SILENCED, False):

File

#### 9.4.2 Que usuarios leen de esta tabla?

In [0]:
%sql
SELECT DISTINCT
  entity_type,
  entity_id,
  source_table_full_name
FROM
  system.lakeflow.table_lineage
WHERE
  source_table_name = 'login_data_silver';


### 9.5 Ejercicio de Creacion de Dashboard

Vamos a crear este dashboard con las tablas de sistema que nos va a permitir poder visualizar informacion referente a nuestro entorno.

Esto nos permitira tener un dashboard que nos aporte una gran cantidad de informacion referente a las ejecuciones que estan sucediendo 

<img src="https://raw.githubusercontent.com/jmartinezceste/251101Course_UC_Ceste/main/photos/DASHBOARD_JOBS.png" width="1300">

Hemos creado una query que nos permite interactuar y crear un dashboard con información relevante a los costes que impactan en nuestro espacio.

Agregaremos la query que alimenta el dashboard y crearemos alguna visualizaciones

- Ve a Dashboards
- Crea un nuevo Dashboards
- añade esta query en la pestaña de "Data"

#### 9.5.1 Query a usar



```sql
-- CTE to fetch the latest job metadata per workspace and job
WITH latest_job_metadata AS (
  SELECT
    *,
    ROW_NUMBER() OVER (
      PARTITION BY workspace_id, job_id 
      ORDER BY change_time DESC
    ) AS rn
  FROM
    system.lakeflow.jobs
  QUALIFY rn = 1
),

-- CTE to fetch the latest cluster metadata per workspace and cluster
latest_clusters_metadata AS (
  SELECT
    *,
    ROW_NUMBER() OVER (
      PARTITION BY workspace_id, cluster_id 
      ORDER BY change_time DESC
    ) AS rn
  FROM
    system.compute.clusters
  QUALIFY rn = 1
),

-- CTE for job run timeline details
jrt AS (
  SELECT
    jr.account_id,
    jr.workspace_id,
    jr.job_id,
    j.name AS job_name,
    j.creator_id,
    j.run_as,
    jr.run_id,
    jr.period_start_time,
    jr.period_end_time,
    jr.trigger_type,
    jr.run_type,
    jr.result_state AS result_state,
    jr.compute_ids,
    (UNIX_TIMESTAMP(jr.period_end_time) - UNIX_TIMESTAMP(jr.period_start_time)) / 60 AS duration_minutes,
    CASE WHEN jr.result_state = 'SUCCEEDED' THEN jr.run_id ELSE NULL END AS success_run_ids,
    CASE WHEN jr.result_state <> 'SUCCEEDED' THEN jr.run_id ELSE NULL END AS failure_run_ids
  FROM
    system.lakeflow.job_run_timeline jr
  JOIN latest_job_metadata j ON jr.job_id = j.job_id
  WHERE
    jr.period_start_time >= DATE(:start_date)
    AND jr.period_start_time < DATE(:end_date) + INTERVAL 1 day
),

-- CTE for pricing
pricing AS (
  SELECT
    p.pricing.effective_list.default AS price_per_unit,
    p.price_start_time,
    p.sku_name,
    COALESCE(p.price_end_time, NOW()) AS price_end_time
  FROM
    system.billing.list_prices p
),

-- CTE with user info, usage, pricing
usage_with_names AS (
  SELECT
    u.account_id,
    u.workspace_id,
    u.usage_metadata['job_id'] AS job_id,
    DATE(u.usage_date) AS usage_date,
    u.sku_name,
    TRANSFORM(
      MAP_KEYS(custom_tags), (k, i) -> CONCAT(
        lower(k),
        '=',
        lower(MAP_VALUES(custom_tags)[i])
      )
    ) AS key_value_tags,
    u.usage_metadata,
    jrt.job_name,
    CASE 
      WHEN REGEXP_REPLACE(
        u.identity_metadata.run_as,
        '([a-zA-Z]+)\\.([a-zA-Z]+)@.*',
        '$1 $2'
      ) = u.identity_metadata.run_as THEN u.identity_metadata.run_as
      ELSE INITCAP(
        REGEXP_REPLACE(
          u.identity_metadata.run_as,
          '([a-zA-Z]+)\\.([a-zA-Z]+)@.*',
          '$1 $2'
        )
      )
    END AS user_name_cleaned,
    jrt.run_id,
    jrt.success_run_ids,
    jrt.failure_run_ids,
    jrt.duration_minutes,
    jrt.result_state,
    jrt.trigger_type,
    SUM(u.usage_quantity) AS usage_quantity, 
    SUM(u.usage_quantity * p.price_per_unit) AS dollar_cost
  FROM
    system.billing.usage u
  LEFT OUTER JOIN jrt ON u.usage_metadata['job_run_id'] = jrt.run_id
    AND u.usage_metadata['job_id'] = jrt.job_id
    AND u.usage_start_time >= DATE_TRUNC("HOUR", jrt.period_start_time)
    AND u.usage_end_time < DATE_TRUNC("HOUR", jrt.period_end_time) + INTERVAL 1 HOUR
  INNER JOIN pricing p ON u.sku_name = p.sku_name
    AND u.usage_start_time BETWEEN p.price_start_time AND p.price_end_time
  WHERE
    u.billing_origin_product = 'JOBS'
    AND u.usage_date >= DATE(:start_date)
    AND u.usage_date < DATE(:end_date) + INTERVAL 1 day
    AND (
      :tags = 'All'
      OR array_contains(
        TRANSFORM(
          MAP_KEYS(custom_tags), (k, i) -> CONCAT(
            lower(k),
            '=',
            lower(MAP_VALUES(custom_tags)[i])
          )
        ),
        :tags
      )
    )
  GROUP BY ALL
),

-- Top k jobs per date
top_jobs_raw AS (
  SELECT
    usage_date,
    job_name,
    SUM(usage_quantity) AS total_usage
  FROM usage_with_names
  GROUP BY usage_date, job_name
),
top_jobs AS (
  SELECT *
  FROM (
    SELECT *,
           ROW_NUMBER() OVER (PARTITION BY usage_date ORDER BY total_usage DESC) AS rn
    FROM top_jobs_raw
  ) t
  WHERE rn <= :top_k
),

-- Top k users per date
top_users_raw AS (
  SELECT
    usage_date,
    user_name_cleaned AS user,
    SUM(usage_quantity) AS total_usage
  FROM usage_with_names
  GROUP BY usage_date, user_name_cleaned
),
top_users AS (
  SELECT *
  FROM (
    SELECT *,
           ROW_NUMBER() OVER (PARTITION BY usage_date ORDER BY total_usage DESC) AS rn
    FROM top_users_raw
  ) t
  WHERE rn <= :top_k
)

-- Final output
SELECT
  uwn.account_id,
  uwn.workspace_id,
  uwn.usage_date,
  uwn.usage_quantity,
  uwn.sku_name,
  key_value_tags,
  uwn.job_id,
  uwn.job_name,
  uwn.run_id,
  uwn.success_run_ids,
  uwn.failure_run_ids,
  uwn.result_state,
  uwn.user_name_cleaned AS user,
  CASE
    WHEN EXISTS (
      SELECT 1 FROM top_jobs tj
      WHERE tj.usage_date = uwn.usage_date AND tj.job_name = uwn.job_name
    ) THEN uwn.job_name
    ELSE 'All Others'
  END AS job_name_group,
  CASE
    WHEN EXISTS (
      SELECT 1 FROM top_users tu
      WHERE tu.usage_date = uwn.usage_date AND tu.user = uwn.user_name_cleaned
    ) THEN uwn.user_name_cleaned
    ELSE 'All Others'
  END AS user_group,
  uwn.duration_minutes,
  uwn.trigger_type,
  uwn.dollar_cost
FROM
  usage_with_names uwn
  ```

#### 9.5.2 Visuales a construir

- Nivel 1:
  - KPI Total Jobs executed: 
      - Tipo Visual: Counter
      - Value: COUNT DISTINCT(run_id)
  - KPI Total DBUs consumed:
      - Tipo Visual: Counter
      - Value: SUM(usage_quantity)
  - KPI Total Cost consumed:
      - Tipo Visual: Counter
      - Value: SUM(dollar_cost)
  - KPI Average JOB duration:
      - Tipo Visual: Counter
      - Value: AVG(duration_minutes)

- Nivel 2:
  - BARCHART Total Cost ($) per JOB:
      - Tipo Visual: Bar
      - X axis: SUM(dollar_cost)
      - Y axis: job_name_group
  - PIECHART Job Status:
      - Tipo Visual: PIE
      - Angle: SUM(dollar_cost)
      - Color: result_state

- Nivel 3:
  - HISTOGRAM Cost ($)  Over time per JOB:
      - Tipo Visual: Bar
      - X axis: DAILY(usage_date)
      - Y axis: SUM(dollar_cost)

- Nivel 4:
  - HISTOGRAM RUNS per day & result_state:
      - Tipo Visual: Bar
      - X axis: DAILY(usage_date)
      - Y axis: COUNT_DISTINCT(run_id)
      - Color: result_state

- Nivel 5: 
  - SUMMARY MATRIX:
      - Tipo Visual: Pivot
      - Rows: job_name, user, workspace_id
      - Columns: result_state
      - Values: SUM(dollar_cost)
